In [5]:
import laser_lib
import numpy as np
import math
import time
import cv2
from skimage.color import rgb2lab, lab2rgb

In [2]:
queue = laser_lib.DacQueue()

Found  1 Helios DACs


In [3]:
def signer(f, T, phase=0.0):
    '''
    Produces spaced out points from 0 to 1 whose distance between 
    consecutive points is sinusoidal 
    Input:  f - frequency 
            T - number of samples
            phase - phase shift (0, 1)
    Returns: x - positions on the line
             dx - the derivative of the function of x
    '''
    # Convert to radians
    f = f*2*np.pi
    # Generate the baseline 
    t = np.linspace(0.0+phase, 1.0+phase, T)
    # Find points 
    x = (f*t - np.cos(f*t) + 1)/f
    # Calculate derivative
    dx = (np.sin(f*t) + 1)/2
    
    return x, dx

def triangle(theta, alpha, sincos='sin'):
    '''
    Returns a wave between a sine wave and triangle wave depending on alpha
    alpha = 0 - sine wave
    alpha = 1 - triangle wave
    '''
    if(sincos == 'sin'):
        ps = 0
    elif(sincos == 'cos'):
        ps = np.pi/2
    return alpha*2*np.arcsin(np.sin(theta + ps))/np.pi + (1-alpha)*np.sin(theta + ps)
    
def ellipser(scale_x=1, scale_y=1, f_x=1, f_y=1, f_s=1000, phase_s=0, sintriang=0, colors=[(1,1,1)], T=500):
    '''
    Generates a pattern that is a function of ellipses 
    with parameters that can be interpolated between
    '''
    theta_norm, theta_dx = signer(f=f_s, phase=phase_s, T=T)
    theta = theta_norm*2*np.pi
    arr_pos = np.zeros((T, 2))
    arr_pos[:,0] = scale_x*triangle(f_x*theta, sintriang, 'sin')
    arr_pos[:,1] = scale_y*triangle(f_y*theta, sintriang, 'cos')
    
    # Color the pattern
    arr_col = np.ones((T, 3), np.float32)
    if(len(colors) == 1):
        # All one color
        arr_col[:, :] = colors[0][np.newaxis, :]
    if(len(colors) == 2):
        # Color based on speed of laser
        arr_col[theta_dx > 0.1, :] = colors[0]
        arr_col[theta_dx <= 0.1, :] = colors[1]
    
    return arr_pos, arr_col


In [4]:
# CIELAB COLOR SPACE
ab_min = -127
ab_max = 128
l_min, l_max  = (0, 130)
num_points = ab_max - ab_min + 1

l = np.linspace(l_min, l_max, num_points)
a = np.linspace(ab_min, ab_max, num_points)
b = np.linspace(ab_min, ab_max, num_points)
l, a, b = np.meshgrid(l, a, b, indexing='ij')
lab = np.stack([l, a, b], axis=-1)

# Convert LAB coords to RGB
rgb = lab2rgb(lab)

for lum in np.concatenate([np.arange(num_points), np.arange(num_points)[::-1]]):
    frame = rgb[lum, :, :, :]
    print('Lum', lum, lab[lum, 0])
    cv2.imshow('frame', cv2.resize(frame, None, fx=2, fy=2))
    cv2.waitKey(10)


/home/bij/anaconda3/envs/Laser/lib/python3.8/site-packages/skimage/color/colorconv.py:1128: UserWarning: Color data out of range: Z < 0 in 1496064 pixels
  return xyz2rgb(lab2xyz(lab, illuminant, observer))


Lum 0 [[   0. -127. -127.]
 [   0. -127. -126.]
 [   0. -127. -125.]
 [   0. -127. -124.]
 [   0. -127. -123.]
 [   0. -127. -122.]
 [   0. -127. -121.]
 [   0. -127. -120.]
 [   0. -127. -119.]
 [   0. -127. -118.]
 [   0. -127. -117.]
 [   0. -127. -116.]
 [   0. -127. -115.]
 [   0. -127. -114.]
 [   0. -127. -113.]
 [   0. -127. -112.]
 [   0. -127. -111.]
 [   0. -127. -110.]
 [   0. -127. -109.]
 [   0. -127. -108.]
 [   0. -127. -107.]
 [   0. -127. -106.]
 [   0. -127. -105.]
 [   0. -127. -104.]
 [   0. -127. -103.]
 [   0. -127. -102.]
 [   0. -127. -101.]
 [   0. -127. -100.]
 [   0. -127.  -99.]
 [   0. -127.  -98.]
 [   0. -127.  -97.]
 [   0. -127.  -96.]
 [   0. -127.  -95.]
 [   0. -127.  -94.]
 [   0. -127.  -93.]
 [   0. -127.  -92.]
 [   0. -127.  -91.]
 [   0. -127.  -90.]
 [   0. -127.  -89.]
 [   0. -127.  -88.]
 [   0. -127.  -87.]
 [   0. -127.  -86.]
 [   0. -127.  -85.]
 [   0. -127.  -84.]
 [   0. -127.  -83.]
 [   0. -127.  -82.]
 [   0. -127.  -81.]
 [   0.

Lum 3 [[   1.52941176 -127.         -127.        ]
 [   1.52941176 -127.         -126.        ]
 [   1.52941176 -127.         -125.        ]
 [   1.52941176 -127.         -124.        ]
 [   1.52941176 -127.         -123.        ]
 [   1.52941176 -127.         -122.        ]
 [   1.52941176 -127.         -121.        ]
 [   1.52941176 -127.         -120.        ]
 [   1.52941176 -127.         -119.        ]
 [   1.52941176 -127.         -118.        ]
 [   1.52941176 -127.         -117.        ]
 [   1.52941176 -127.         -116.        ]
 [   1.52941176 -127.         -115.        ]
 [   1.52941176 -127.         -114.        ]
 [   1.52941176 -127.         -113.        ]
 [   1.52941176 -127.         -112.        ]
 [   1.52941176 -127.         -111.        ]
 [   1.52941176 -127.         -110.        ]
 [   1.52941176 -127.         -109.        ]
 [   1.52941176 -127.         -108.        ]
 [   1.52941176 -127.         -107.        ]
 [   1.52941176 -127.         -106.        ]
 [  

Lum 13 [[   6.62745098 -127.         -127.        ]
 [   6.62745098 -127.         -126.        ]
 [   6.62745098 -127.         -125.        ]
 [   6.62745098 -127.         -124.        ]
 [   6.62745098 -127.         -123.        ]
 [   6.62745098 -127.         -122.        ]
 [   6.62745098 -127.         -121.        ]
 [   6.62745098 -127.         -120.        ]
 [   6.62745098 -127.         -119.        ]
 [   6.62745098 -127.         -118.        ]
 [   6.62745098 -127.         -117.        ]
 [   6.62745098 -127.         -116.        ]
 [   6.62745098 -127.         -115.        ]
 [   6.62745098 -127.         -114.        ]
 [   6.62745098 -127.         -113.        ]
 [   6.62745098 -127.         -112.        ]
 [   6.62745098 -127.         -111.        ]
 [   6.62745098 -127.         -110.        ]
 [   6.62745098 -127.         -109.        ]
 [   6.62745098 -127.         -108.        ]
 [   6.62745098 -127.         -107.        ]
 [   6.62745098 -127.         -106.        ]
 [ 

Lum 22 [[  11.21568627 -127.         -127.        ]
 [  11.21568627 -127.         -126.        ]
 [  11.21568627 -127.         -125.        ]
 [  11.21568627 -127.         -124.        ]
 [  11.21568627 -127.         -123.        ]
 [  11.21568627 -127.         -122.        ]
 [  11.21568627 -127.         -121.        ]
 [  11.21568627 -127.         -120.        ]
 [  11.21568627 -127.         -119.        ]
 [  11.21568627 -127.         -118.        ]
 [  11.21568627 -127.         -117.        ]
 [  11.21568627 -127.         -116.        ]
 [  11.21568627 -127.         -115.        ]
 [  11.21568627 -127.         -114.        ]
 [  11.21568627 -127.         -113.        ]
 [  11.21568627 -127.         -112.        ]
 [  11.21568627 -127.         -111.        ]
 [  11.21568627 -127.         -110.        ]
 [  11.21568627 -127.         -109.        ]
 [  11.21568627 -127.         -108.        ]
 [  11.21568627 -127.         -107.        ]
 [  11.21568627 -127.         -106.        ]
 [ 

...

Lum 43 [[  21.92156863 -127.         -127.        ]
 [  21.92156863 -127.         -126.        ]
 [  21.92156863 -127.         -125.        ]
 [  21.92156863 -127.         -124.        ]
 [  21.92156863 -127.         -123.        ]
 [  21.92156863 -127.         -122.        ]
 [  21.92156863 -127.         -121.        ]
 [  21.92156863 -127.         -120.        ]
 [  21.92156863 -127.         -119.        ]
 [  21.92156863 -127.         -118.        ]
 [  21.92156863 -127.         -117.        ]
 [  21.92156863 -127.         -116.        ]
 [  21.92156863 -127.         -115.        ]
 [  21.92156863 -127.         -114.        ]
 [  21.92156863 -127.         -113.        ]
 [  21.92156863 -127.         -112.        ]
 [  21.92156863 -127.         -111.        ]
 [  21.92156863 -127.         -110.        ]
 [  21.92156863 -127.         -109.        ]
 [  21.92156863 -127.         -108.        ]
 [  21.92156863 -127.         -107.        ]
 [  21.92156863 -127.         -106.        ]
 [ 

Lum 34 [[  17.33333333 -127.         -127.        ]
 [  17.33333333 -127.         -126.        ]
 [  17.33333333 -127.         -125.        ]
 [  17.33333333 -127.         -124.        ]
 [  17.33333333 -127.         -123.        ]
 [  17.33333333 -127.         -122.        ]
 [  17.33333333 -127.         -121.        ]
 [  17.33333333 -127.         -120.        ]
 [  17.33333333 -127.         -119.        ]
 [  17.33333333 -127.         -118.        ]
 [  17.33333333 -127.         -117.        ]
 [  17.33333333 -127.         -116.        ]
 [  17.33333333 -127.         -115.        ]
 [  17.33333333 -127.         -114.        ]
 [  17.33333333 -127.         -113.        ]
 [  17.33333333 -127.         -112.        ]
 [  17.33333333 -127.         -111.        ]
 [  17.33333333 -127.         -110.        ]
 [  17.33333333 -127.         -109.        ]
 [  17.33333333 -127.         -108.        ]
 [  17.33333333 -127.         -107.        ]
 [  17.33333333 -127.         -106.        ]
 [ 

Lum 24 [[  12.23529412 -127.         -127.        ]
 [  12.23529412 -127.         -126.        ]
 [  12.23529412 -127.         -125.        ]
 [  12.23529412 -127.         -124.        ]
 [  12.23529412 -127.         -123.        ]
 [  12.23529412 -127.         -122.        ]
 [  12.23529412 -127.         -121.        ]
 [  12.23529412 -127.         -120.        ]
 [  12.23529412 -127.         -119.        ]
 [  12.23529412 -127.         -118.        ]
 [  12.23529412 -127.         -117.        ]
 [  12.23529412 -127.         -116.        ]
 [  12.23529412 -127.         -115.        ]
 [  12.23529412 -127.         -114.        ]
 [  12.23529412 -127.         -113.        ]
 [  12.23529412 -127.         -112.        ]
 [  12.23529412 -127.         -111.        ]
 [  12.23529412 -127.         -110.        ]
 [  12.23529412 -127.         -109.        ]
 [  12.23529412 -127.         -108.        ]
 [  12.23529412 -127.         -107.        ]
 [  12.23529412 -127.         -106.        ]
 [ 

Lum 14 [[   7.1372549 -127.        -127.       ]
 [   7.1372549 -127.        -126.       ]
 [   7.1372549 -127.        -125.       ]
 [   7.1372549 -127.        -124.       ]
 [   7.1372549 -127.        -123.       ]
 [   7.1372549 -127.        -122.       ]
 [   7.1372549 -127.        -121.       ]
 [   7.1372549 -127.        -120.       ]
 [   7.1372549 -127.        -119.       ]
 [   7.1372549 -127.        -118.       ]
 [   7.1372549 -127.        -117.       ]
 [   7.1372549 -127.        -116.       ]
 [   7.1372549 -127.        -115.       ]
 [   7.1372549 -127.        -114.       ]
 [   7.1372549 -127.        -113.       ]
 [   7.1372549 -127.        -112.       ]
 [   7.1372549 -127.        -111.       ]
 [   7.1372549 -127.        -110.       ]
 [   7.1372549 -127.        -109.       ]
 [   7.1372549 -127.        -108.       ]
 [   7.1372549 -127.        -107.       ]
 [   7.1372549 -127.        -106.       ]
 [   7.1372549 -127.        -105.       ]
 [   7.1372549 -127.       

Lum 4 [[   2.03921569 -127.         -127.        ]
 [   2.03921569 -127.         -126.        ]
 [   2.03921569 -127.         -125.        ]
 [   2.03921569 -127.         -124.        ]
 [   2.03921569 -127.         -123.        ]
 [   2.03921569 -127.         -122.        ]
 [   2.03921569 -127.         -121.        ]
 [   2.03921569 -127.         -120.        ]
 [   2.03921569 -127.         -119.        ]
 [   2.03921569 -127.         -118.        ]
 [   2.03921569 -127.         -117.        ]
 [   2.03921569 -127.         -116.        ]
 [   2.03921569 -127.         -115.        ]
 [   2.03921569 -127.         -114.        ]
 [   2.03921569 -127.         -113.        ]
 [   2.03921569 -127.         -112.        ]
 [   2.03921569 -127.         -111.        ]
 [   2.03921569 -127.         -110.        ]
 [   2.03921569 -127.         -109.        ]
 [   2.03921569 -127.         -108.        ]
 [   2.03921569 -127.         -107.        ]
 [   2.03921569 -127.         -106.        ]
 [  

In [33]:
# Sampling the CIELAB Space
AB_choices = np.arange(start, stop+1).astype(np.float32)
while(True):
    # Choose a Lum
    lum_c = int(100*np.random.rand(1))
    # Choose an A
    a_c = np.random.choice(AB_choices)
    # Choose a B 
    b_c = np.random.choice(AB_choices)

    try:
        point_rgb = lab2rgb([[lum_c, a_c, b_c]])
        point_rgb_opp = lab2rgb((lum_c, -1*a_c, -1*b_c))
    except:
        # Skip this invalid combo
        continue
    print((lum_c, a_c, b_c), point_rgb)
    

    frame = np.zeros((400, 200, 3))
    frame[0:200, :, :] = point_rgb
    frame[200:400, :, :] = point_rgb_opp
    cv2.imshow('point', frame)
    cv2.waitKey(1000)


(18, -62.0, 82.0) [[0.         0.22866406 0.        ]]
(30, -20.0, 12.0) [[0.16434383 0.3073898  0.20145151]]
(50, -13.0, 108.0) [[0.50371245 0.48163237 0.        ]]
(38, -11.0, -32.0) [[0.        0.3810198 0.5524043]]
(69, 16.0, 99.0) [[0.88884314 0.6068961  0.        ]]
(57, -88.0, -58.0) [[0.         0.6777004  0.93020421]]
(17, -87.0, 11.0) [[0.         0.24005605 0.09339793]]
(58, 7.0, -127.0) [[0.         0.60557558 1.        ]]
(21, 33.0, -15.0) [[0.33652258 0.10665319 0.28662521]]
(45, 120.0, 77.0) [[1. 0. 0.]]
(39, 50.0, 104.0) [[0.68626291 0.1711163  0.        ]]
(39, 80.0, 104.0) [[0.81593277 0.         0.        ]]
(14, -61.0, 29.0) [[0.         0.19793232 0.        ]]
(57, 16.0, -5.0) [[0.63073781 0.49972431 0.57208634]]
(78, 5.0, 85.0) [[0.93157017 0.7302315  0.        ]]
(59, 90.0, 122.0) [[1. 0. 0.]]
(15, -71.0, -35.0) [[0.        0.2243911 0.3416695]]
(20, 87.0, 33.0) [[0.58691912 0.         0.01300651]]
(85, 115.0, 9.0) [[1.         0.20681352 0.78813118]]
(26, 122.0,

KeyboardInterrupt: 

In [15]:
# Make spiral of CIELab
T = 1000
turns = 7
theta = np.linspace(0, 2*np.pi*turns, T)
scale = np.linspace(0, 1, T)

arr_pos = np.zeros((T, 2))
arr_pos[:, 0] = scale*np.cos(theta)
arr_pos[:, 1] = scale*np.sin(theta)

arr_col_lab = np.zeros((T, 3))
arr_col_lab[:, 0] = (l_max-l_min)*np.sqrt(arr_pos[:, 0]**2 + arr_pos[:, 1]**2) + l_min
w = (l_max-l_min)*scale + l_min
arr_col_lab[:, 1] = (ab_max-ab_min)*(arr_pos[:, 0]+1)/2 + ab_min
arr_col_lab[:, 2] = (ab_max-ab_min)*(arr_pos[:, 1]+1)/2 + ab_min

arr_col_rgb = lab2rgb(arr_col_lab)

queue.dac_rate = 40000
for step in range(1000):
    queue.submit(arr_pos, arr_col_rgb)
    #queue.submit(arr_pos[::-1], arr_col_rgb[::-1])

In [7]:
# Interpolated ellipses
T = 750
arr_col = np.ones((T, 3))
theta = np.linspace(0, 2*np.pi, T)

min_vals = np.array([0.5, 0.0, 0.5, 0.0, 0.0, 0.0, 0.0, 0.1, 0.1, 0.1, 0.1, 0.1, 0.1])
max_vals = np.array([1.0, 0.4, 2.0, 3.0, 1.0, 0.5, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0])
pat_point_old = (max_vals-min_vals)*np.random.rand(len(max_vals)) + min_vals


T_trans = 150

while(True):
    pat_point = (max_vals-min_vals)*np.random.rand(len(max_vals)) + min_vals
    ell_interp = np.linspace(pat_point_old, pat_point, T_trans)
    for (scale_x, scale_y, freq_x, freq_y, f_s, phase, sintriang, r1, g1, b1, r2, g2, b2) in ell_interp:
        # Transform the distribution of f_s to be less uniform
        f_s = 40*np.power(f_s, 6)
        #TODO - transform sintriang to have a bathtub curve
        
        # Get the array
        arr_pos, arr_col = ellipser(scale_x=scale_x, 
                                    scale_y=scale_y, 
                                    f_x=freq_x, 
                                    f_y=freq_y, 
                                    f_s=f_s, 
                                    phase_s=phase,
                                    sintriang=sintriang, 
                                    colors=[(r1,g1,b1), (r2,g2,b2)],
                                    T=T)
        
        queue.submit(arr_pos, np.roll(arr_col, shift=9, axis=0))
        
    pat_point_old = pat_point

KeyboardInterrupt: 

In [63]:
# Interpolated ellipses
T = 750
arr_col = np.ones((T, 3))
theta = np.linspace(0, 2*np.pi, T)



(r1,g1,b1) = (0, 0.1, 0.1)
(r2,g2,b2) = (1.0, 0.4, 0.4)
for shift in range(-10, 10):
    print(shift)
    for i in range(100):
        arr_pos, arr_col = ellipser(scale_x=1.0, 
                                    scale_y=1.0, 
                                    f_x=1.0, 
                                    f_y=1.0, 
                                    f_s=10, 
                                    phase_s=0.0,
                                    sintriang=0.0, 
                                    colors=[(r1,g1,b1), (r2,g2,b2)],
                                    T=T)

        queue.submit(arr_pos, np.roll(arr_col, shift, axis=0))
        


-10
-9
-8
-7
-6
-5
-4
-3
-2
-1
0
1
2
3
4


KeyboardInterrupt: 

In [6]:
# Align mirrors and laser 
T = 1000
turns = 7
theta = np.linspace(0, 2*np.pi*turns, T)

arr_pos = np.zeros((T, 2))
arr_pos[:, 0] = np.linspace(-1.0, 1.0, T)
arr_pos[:, 1] = np.sin(theta)

arr_col = np.zeros((T, 3))
#arr_col[:, 0] = np.abs(arr_pos[:, 1]) > 0.99
arr_col[:, 0] = np.abs(arr_pos[:, 1]) > 0.999
arr_col[:, 1] = np.abs(arr_pos[:, 1]) > 0.999
arr_col[:, 2] = np.abs(arr_pos[:, 1]) > 0.999

# Corresponds to Red, Green, Blue @ dac_rate 55k
shifts = [11, 10, 9]

# Correct color array by shifting
#for col_idx  in range(3):
#    arr_col[:, col_idx] = np.roll(arr_col[:, col_idx], shifts[col_idx], axis=0)
    
#for col_idx, shift in enumerate(shifts):
#    print(col_idx, shift)
#    arr_col[:, col_idx] = np.roll(arr_col[:, col_idx], shift, axis=0)

for shift in range(8, 20):
    print(shift)
    for i in range(100):
        queue.submit(arr_pos, arr_col)

8
9
10
11
12
13
14
15
16
17
18
19
